# Data Cleaning

This notebook intends to show the user how raw data coming from non-standardised database can be clean using the Pandas library. Here is used the hyperspectral dataset coming from the CSIRO. Row dataset has been added to GeoLime dataset in order to avoid user from downloading it.

In [ ]:
import pandas as pd
import geolime as geo

## Format Pandas display for clarity and readability
For clarity and readability, Pandas display can be updated to show only 10 rows and display all the columns. By default, Pandas displays DataFrame with 20 columns and 60 rows. For this dataset this would mean hiding some columns and displaying too many rows, hence polluting the notebook.

In [ ]:
pd.set_option("display.max_rows", 10)
pd.set_option("display.max_columns", 500)

## Import Data

Rocklea Dome open dataset is included in GeoLime in order to facilitate the startup. Avalaibles dataset can be listed using the command `geo.datasets.list_datasets` and availables data in the Rocklea Dome datasets can be listed using the command `geo.datasets.list_data("rocklea_dome")`.

In [ ]:
hs_assay = geo.datasets.load("rocklea_dome/RC_data_tsgexport.csv")

In [ ]:
hs_assay

To ensure values from a same hole follows each other in the table, we sort the values by their `Borehole ID`, we use the `inplace` parameter in order to modify the original DataFrame directly.

In [ ]:
hs_assay.sort_values(by="Borehole ID", inplace=True)

Otherwise we would need to do something of the like 
```python
hs_assay = hs_assay.sort_values(by="Borehole ID")
```

## Check for invalid composites

Invalid composite are composite that either have :
 - no hole identifier 
 - no depth from information

We first check if they are rows with no `Borehole ID`. To do so we access the DataFrame at the rows where the DataFrame does not have a value in the given column.

In [ ]:
hs_assay[hs_assay["Borehole ID"].isna()]

378 composites do not have any hole identifiant `Borehole ID`, they cannot be used and are then dropped.

In [ ]:
hs_assay.dropna(subset=["Borehole ID"], inplace=True)

We then check if they are rows with no `Depth from`. To do so we access the DataFrame at the rows where the DataFrame does not have a value in the given column.

In [ ]:
hs_assay[hs_assay["Depth from"].isna()] 

8 composites do not have a given `Depth From`, making them unusable. It seems the `Sample Name` column contains some depth information, but there is no information about this column, we prefer to discard any sample with doubts.

In [ ]:
hs_assay.dropna(subset=["Depth from"], inplace=True)

## Check for duplicate composites

Duplicated composite cannot be kept as this would mean we have two information at the same location. To do so we use the duplicated pandas method, which will return a boolean series where rows are duplicated. By default the method check the values of all columns, here we juste need to check the spatial duplicated using `Borehole ID` and `Depth from`. 

In [ ]:
hs_assay[hs_assay.duplicated(subset=["Borehole ID", "Depth from"],keep=False)]

51 composites appear to be defined at the same depth, we will remove the column with the most number of NaN values. 

:::{admonition} Discard based on other criterion
:class: tip
Other rules could be implemented, for example regarding the value in Iron and remove the possible outlier. 
:::

We first compute the number of NaN values per row:

In [ ]:
hs_assay["number_of_NaNs"] = hs_assay[hs_assay.columns].isna().sum(1)

Then we sort the DataFrame by `Borehole ID`, `Depth from` and number of NaN, and first row is kept.

In [ ]:
hs_assay.sort_values(by=["Borehole ID", "Depth from", "number_of_NaNs"], ascending=[True, True, False], inplace=True)
hs_assay.drop_duplicates(subset=["Borehole ID", "Depth from"], keep="first", inplace=True)

## Remove unneeded columns

We can delete the first two columns and rename the third one into `Hole_ID` in order to matchv the other files nomenclature. We will need identical names to be able to make comparisons between the files. We also delete location information as they are given in the collar file. The created column used for filtering duplicates is also removed.

In [ ]:
hs_assay = hs_assay.drop(columns=["Sample", "Sample Name", "Easting", "Northing", "number_of_NaNs"])

Spaces and special characters are not recommended as they can be source of error and conflicts depending on the operating systems. The ambiguity of special characters in programmation can also be a source of errors.
User can specify property unit in GeoLime, see it section 2 - `Drillholes creation and quick visualization`

In [ ]:
hs_assay.columns = hs_assay.columns.str.replace(" ", "_")
hs_assay.columns = hs_assay.columns.str.replace("_%", "_pct")
hs_assay.columns = hs_assay.columns.str.replace("/", "_over_")

We rename columns using shorter names

In [ ]:
hs_assay.rename(columns={"Borehole_ID": "Hole_ID", "Depth_from": "From"}, inplace=True)
hs_assay

The following modification is very situational, but in our case the Hole_IDs are lowercase, while in the Collar and Survey files this is not the case, and since the names must match between the files, we will apply this function to the Hole_ID column:

In [ ]:
hs_assay["Hole_ID"] = hs_assay["Hole_ID"].apply(str.upper)
hs_assay

## Add `To` Column 

To complete the file we need to add a new column that indicates the depth where each sample stops, the column `To`. Here composite all have the same length of 1m. 

First we ensure the DataFrame is sorted by `Hole_ID` and in each `Hole_ID` values are sorted by the `From` values.

In [ ]:
hs_assay.sort_values(by=["Hole_ID", "From"], inplace=True)
hs_assay

We create a new column `To` consisting of the `From` values plus one. We use the insert method as we want this column to be in third position (recall in python things beginn at index 0).

In [ ]:
hs_assay.insert(2, "To", hs_assay["From"] + 1)
hs_assay

To organize these datas we can group them in ascendant `Hole_ID` and ascendant `From` so we will have every borehole in alphabetic order and for every borehole its samples from the most superficial to the deepest.

This last correction is again very situational, but in our case we had to create on the spreadsheet the column "To" on the basis of the column "From". The problem is that this kind of manipulation sometimes results in a wrong type of value in these boxes, so we will apply a function to put everything in float.

In [ ]:
hs_assay["To"] = pd.to_numeric(hs_assay["To"], downcast="float")

In [ ]:
hs_assay.to_csv("../data/hyperspec.csv", index=False)